In [1]:
from hicmatrix import HiCMatrix as hm
from hicmatrix.lib import MatrixFileHandler
import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck
from scipy.stats import mannwhitneyu
import h5py
import os.path
import gc
import os
import matplotlib.pyplot as plt


from umap import UMAP

from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
import scipy.spatial as sp, scipy.cluster.hierarchy as hc

import seaborn as sns
%matplotlib inline


INFO:numexpr.utils:Note: NumExpr detected 32 cores but "NUMEXPR_MAX_THREADS" not set, so enforcing safe limit of 8.
INFO:numexpr.utils:NumExpr defaulting to 8 threads.


In [2]:
import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
sns.set(style='white', font_scale=1)
plt.rc("axes.spines", top=False, right=False)
plt.rc('xtick', bottom=True)
plt.rc('ytick', left=True)
import joypy

In [3]:
def marker_list_gene_symbol(marker_list, species):
    if species == "human":
        marker_list['gene'] = marker_list['gene'].str.upper()
        df_ensg_name = pd.read_csv(f'{base_folder}/hi_c_data_processing/genomes_jlee/ensg_geneid_symbol.csv', sep='\t')[['Ensembl_gene_identifier', 'Symbol']]
        
    else:
        df_ensg_name = pd.read_csv(f'{base_folder}/hi_c_data_processing/genomes_jlee//mouse_geneid_symbol.txt', sep='\t', names=['Ensembl_gene_identifier', 'Symbol'])

    

    marker_list = marker_list.merge(df_ensg_name.drop_duplicates(), right_on='Symbol', left_on='gene') 
    
    return marker_list


In [4]:
def marker_list_gene_symbol(marker_list, species):
    if species == "human":
        marker_list['gene'] = marker_list['gene'].str.upper()
        df_ensg_name = pd.read_csv(f'{base_folder}/hi_c_data_processing/genomes_jlee/ensg_geneid_symbol.csv', sep='\t')[['Ensembl_gene_identifier', 'Symbol']]
        
    else:
        df_ensg_name = pd.read_csv(f'{base_folder}/hi_c_data_processing/genomes_jlee//mouse_geneid_symbol.txt', sep='\t', names=['Ensembl_gene_identifier', 'Symbol'])

    

    marker_list = marker_list.merge(df_ensg_name.drop_duplicates(), right_on='Symbol', left_on='gene') 
    
    return marker_list


In [5]:
#obtain mouse marker list
base_folder='/grid/gillis/data_norepl/lohia'
marker_list_mouse_brain = pd.read_csv(f'{base_folder}/hi_c_data_processing/notebooks/metamarkers/mouse/joint_subclass_markers.csv.gz', skiprows=1)
marker_list_mouse_brain_type = pd.read_csv(f'{base_folder}/hi_c_data_processing/notebooks/metamarkers/mouse/joint_cluster_markers.csv.gz', skiprows=1)
marker_list_mouse_blood = marker_list = pd.read_csv(f'{base_folder}/blood_ben/media-2.csv')


marker_list_human_brain = pd.read_csv(f'{base_folder}/hi_c_data_processing/notebooks/metamarkers/human/subclass_markers_top1000.csv.gz', skiprows=1)
marker_list_human_brain_class = pd.read_csv(f'{base_folder}/hi_c_data_processing/notebooks/metamarkers/human/class_markers_top1000.csv.gz', skiprows=1)
marker_list_human_brain_type = pd.read_csv(f'{base_folder}/hi_c_data_processing/notebooks/metamarkers/human/type_markers_top1000.csv.gz', skiprows=1)

marker_list_list = []
marker_list = pd.read_csv('/grid/gillis/data_norepl/lohia/heart_hamsini/Knight-Schrijver_celltype_markers_res2.csv.gz', skiprows=1)
all_cell_types = marker_list.drop_duplicates(['cell_type'])['cell_type'].tolist()
for group2 in all_cell_types:

                m_tmp = marker_list[marker_list['cell_type']==group2]
                m_tmp['recurrence'] = 1
                m_tmp['n_datasets'] = 1

                m_tmp['rank'] = [x+1 for x in range(m_tmp.shape[0])]
                marker_list_list.append(m_tmp)
marker_list = pd.concat(marker_list_list)
marker_list_human_heart = marker_list

/home/lohia/miniconda3/envs/hicexplorer/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (13,14,15,16,18) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,
/home/lohia/miniconda3/envs/hicexplorer/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (13,14,15,16,18,19) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,
/home/lohia/miniconda3/envs/hicexplorer/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (18,19,20,21) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,
/home/lohia/miniconda3/envs/hicexplorer/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (13,15,18,20,21)

In [6]:
marker_list_input_dict = {}
species='mouse'

marker_list_input_dict[species] = pd.concat([marker_list_gene_symbol(marker_list_mouse_brain, species), marker_list_gene_symbol(marker_list_mouse_brain_type, species), marker_list_gene_symbol(marker_list_mouse_blood, species)])


species='human'

marker_list_input_dict[species] = pd.concat([marker_list_gene_symbol(marker_list_human_brain, species), marker_list_gene_symbol(marker_list_human_brain_type, species), marker_list_gene_symbol(marker_list_human_heart, species)])




In [6]:
def get_input_matrix(species, SRP_name, resolution, process_type, marker_list):
    
    
    cat_list_genes = marker_list['Ensembl_gene_identifier'].drop_duplicates().tolist()
    #cat_list_genes = marker_table.index.tolist()
    input_path=f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/'
    bins_bed = pd.read_csv(f'{input_path}/all_bins_max.bed', names=['chr', 'start', 'end', 'bin_id'])
    bins_bed['bin_id'] = bins_bed.index

    bins_bed.to_csv(f'{input_path}/all_bins_true.bed', index=False, header=False, sep='\t')

    chr_list = bins_bed.drop_duplicates(subset=['chr'])['chr'].tolist()

   

    df_genes_chrom = pd.read_csv(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/all_gene_max.bed', names=['chrom', 'st', 'end', 'gene'])
                
    
    with h5py.File(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/hic_gene_gw_none_by_allbins_none_max.h5', 'r') as hf:
            tot_g = (list(hf.keys()))
    
    if resolution == '1kbp_raw':
        prec = 'float32'
    else:
        prec = 'float32'
    
    finite_list = []
    gene_list_list = []
    chrn_write_list_list = []
    my_data_thresh_list = []
    gene_depth_list = []
    
    marker_contacts_list_inter = []

    gene_list = []
        
    chrn_write_list = []
    
    marker_contacts_list_inter_thresholded = []
    
    for each_chrom in chr_list:
      
        
       


            with h5py.File(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/hic_gene_gw_none_by_allbins_none_max.h5', 'r') as hf:

                               #for key in all_background_markers:
                               for key, m_chrom in zip(df_genes_chrom['gene'].tolist(), df_genes_chrom['chrom'].tolist()):
                                  #if key in tot_g:
                                    if key in cat_list_genes:
                                    
                                      if m_chrom == each_chrom:
                                            gene_list.append(key)


                                            #gene_chrom = gene_bed[gene_bed['gene'] == key]['chr'].values[0]
                                            #which ever chrom the gene falls into, those bins should be nan
                                            my_data = hf[key][()]
                                            my_data = my_data.astype(prec)
                                            #my_data[chrom_index_list[each_chrom]] = np.nan
                                            #print (my_data)
                                            #gene_depth_list.append(bottleneck.nansum(my_data))
                                            marker_contacts_list_inter.append(my_data)
                                            
                                            
                                            
                                            #my_data[my_data != 0] = 1
                                            #print (my_data)
                                            
                                            #my_data[chrom_index_list[each_chrom]] = np.nan
                                            #print (my_data)
                                            #marker_contacts_list_inter_thresholded.append(my_data)
                                            
                                            



    my_data = np.array(marker_contacts_list_inter)
    df_gene_tp = pd.DataFrame(my_data ,  index=gene_list, columns = bins_bed['bin_id'].tolist())
    #my_data = df_gene_tp.loc[:, pure_bins]
    
    #my_data_binarized = np.array(marker_contacts_list_inter_thresholded)
    #df_gene_tp_binarized = pd.DataFrame(my_data_binarized ,  index=gene_list, columns = bins_bed['bin_id'].tolist())
    #df_gene_tp_binarized = df_gene_tp_binarized.loc[:, pure_bins]
    
    
    



    
    return (df_gene_tp)
                                    
    

In [8]:
df_zscore = {}

In [7]:
process_type='inter'
SRP_name='aggregates'

for species in ['human']:
    for resolution in ['250kbp_raw']:
        print ("j")

j


In [ ]:
process_type='inter'
SRP_name='aggregates'

for species in ['human']:
    for resolution in ['250kbp_raw']:
        df_zscore[(species, resolution, 'raw_count')] = get_input_matrix(species, SRP_name, resolution, process_type, marker_list_input_dict[species].head().drop_duplicates(['Ensembl_gene_identifier']))


In [8]:
    with h5py.File(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/hic_gene_gw_none_by_allbins_none_max.h5', 'r') as hf:
            tot_g = (list(hf.keys()))
            